## Downloading libraries

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done


==> WARNING: A newer version of conda exists. <==
  current version: 4.5.11
  latest version: 4.7.11

Please update conda by running

    $ conda update -n base -c defaults conda



## Package Plan ##

  environment location: /home/jupyterlab/conda/envs/python

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    geopy-1.20.0               |             py_0          57 KB  conda-forge
    geographiclib-1.49         |             py_0          32 KB  conda-forge
    ------------------------------------------------------------
                                           Total:          90 KB

The following NEW packages will be INSTALLED:

    geographiclib: 1.49-py_0   conda-forge
    geopy:         1.20.0-py_0 conda-forge


geopy-1.20.0         | 57 KB     | ##################################### | 100% 
geographiclib-1.49   | 

<a id='item1'></a>

## Download and Explore Dataset

Data with the latitude and logitude coordinates of each neighborhood. 

The link to the dataset: https://geo.nyu.edu/catalog/nyu_2451_34572

In [2]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


loading the data

In [3]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [4]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

neighborhoods_data includes a list of the neighborhoods

In [5]:
neighborhoods_data = newyork_data['features']

#### Tranform the data into a *pandas* dataframe

In [6]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

Looping through the data and filling the dataframe one row at a time.

In [8]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [9]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [10]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


#### Use geopy library to get the latitude and longitude values of New York City.

ny_explorer is an instance of the geocoder

In [11]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


## A map of New York with neighborhoods superimposed on top.

In [12]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

**Folium** is a great visualization library. Feel free to zoom into the above map, and click on each circle mark to reveal the name of the neighborhood and its respective borough.

Utilizing the Foursquare API to explore the neighborhoods and segment them.

#### Define Foursquare Credentials and Version

In [13]:
CLIENT_ID = '1WOG2OFV2HGHNO51XYQ4EBU0QSAUSGFVT5Y5BGX51GPRD4YC' # your Foursquare ID
CLIENT_SECRET = 'B2WRM1EARLL5INHEF4VOYGUEXKYBDWDROSMND2W312NQFBHR' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 1WOG2OFV2HGHNO51XYQ4EBU0QSAUSGFVT5Y5BGX51GPRD4YC
CLIENT_SECRET:B2WRM1EARLL5INHEF4VOYGUEXKYBDWDROSMND2W312NQFBHR


<a id='item2'></a>

## Explore Neighborhoods in New York

In [20]:
LIMIT = 100
radius = 500

def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

### Run the above function on each neighborhood and create a new dataframe called newyork_venues

In [21]:
newyork_venues = getNearbyVenues(names=neighborhoods['Neighborhood'],
                                   latitudes=neighborhoods['Latitude'],
                                   longitudes=neighborhoods['Longitude']
                                  )

Wakefield
Co-op City
Eastchester
Fieldston
Riverdale
Kingsbridge
Marble Hill
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
City Island
Bedford Park
University Heights
Morris Heights
Fordham
East Tremont
West Farms
High  Bridge
Melrose
Mott Haven
Port Morris
Longwood
Hunts Point
Morrisania
Soundview
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Pelham Bay
Schuylerville
Edgewater Park
Castle Hill
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Bay Ridge
Bensonhurst
Sunset Park
Greenpoint
Gravesend
Brighton Beach
Sheepshead Bay
Manhattan Terrace
Flatbush
Crown Heights
East Flatbush
Kensington
Windsor Terrace
Prospect Heights
Brownsville
Williamsburg
Bushwick
Bedford Stuyvesant
Brooklyn Heights
Cobble Hill
Carroll Gardens
Red Hook
Gowanus
Fort Greene
Park Slope
Cypress Hills
East New York
Starrett City
Canarsie
Flatlands
Mill Island
Manhattan Beach
Coney Island
Bath Beach
Borough Park
Dyker

#### The size of the resulting dataframe

In [22]:
print(newyork_venues.shape)
newyork_venues.head()

(10412, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

                                     Venue  Venue Latitude  Venue Longitude  \
0                         Lollipops Gelato       40.894123       -73.845892   
1                                 Rite Aid       40.896649       -73.844846   
2                         Carvel Ice Cream       40.890487       -73.848568   
3  Cooler Runnings Jamaican Restaurant Inc       40.898276       -73.850381   
4                                  Dunkin'       40.890459       -73.849089   

         Venue Category  
0          Dessert Shop  
1              Pharmacy  
2        Ice Cream Shop  
3  Caribbean Restaurant  
4            Donut Shop

## Number of venues were returned for each neighborhood

In [23]:
newyork_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Allerton                                      28                      28   
Annadale                                      10                      10   
Arden Heights                                  4                       4   
Arlington                                      7                       7   
Arrochar                                      20                      20   
Arverne                                       18                      18   
Astoria                                      100                     100   
Astoria Heights                               15                      15   
Auburndale                                    19                      19   
Bath Beach                                    51                      51   
Battery Park City                            100                     100   
Bay Ridge                                     83                      83   
Bay Terrace                                   49                      49   
Baychester                                    20                      20   
Bayside                                       71                      71   
Bayswater                                      2                       2   
Bedford Park                                  41                      41   
Bedford Stuyvesant                            30                      30   
Beechhurst                                    13                      13   
Bellaire                                      11                      11   
Belle Harbor                                  18                      18   
Bellerose                                     21                      21   
Belmont                                      100                     100   
Bensonhurst                                   29                      29   
Bergen Beach                                   7                       7   
Blissville                                    21                      21   
Bloomfield                                     5                       5   
Boerum Hill                                   88                      88   
Borough Park                                  20                      20   
Breezy Point                                   5                       5   
Briarwood                                     12                      12   
Brighton Beach                                44                      44   
Broad Channel                                  7                       7   
Broadway Junction                             15                      15   
Bronxdale                                     14                      14   
Brooklyn Heights                             100                     100   
Brookville                                     2                       2   
Brownsville                                   19                      19   
Bulls Head                                    44                      44   
Bushwick                                      77                      77   
Butler Manor                                   6                       6   
Cambria Heights                               14                      14   
Canarsie                                       5                       5   
Carnegie Hill                                100                     100   
Carroll Gardens                              100                     100   
Castle Hill                                   11                      11   
Castleton Corners                             15                      15   
Central Harlem                                45                      45   
Charleston                                    31                      31   
Chelsea                                      104                     104   
Chinatown                                    100                     100   

#### Number of unique categories from all the returned venues

In [24]:
print('There are {} uniques categories.'.format(len(newyork_venues['Venue Category'].unique())))

There are 431 uniques categories.


<a id='item3'></a>

## Analyze Each Neighborhood

In [25]:

newyork_onehot = pd.get_dummies(newyork_venues[['Venue Category']], prefix="", prefix_sep="")

newyork_onehot['Neighborhood'] = newyork_venues['Neighborhood'] 

fixed_columns = [newyork_onehot.columns[-1]] + list(newyork_onehot.columns[:-1])
newyork_onehot = newyork_onehot[fixed_columns]

newyork_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            0                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   African Restaurant  American Restaurant  Antique Shop  Arcade  \
0                   0                    0             0       0   
1                   0                    0             0       0   
2                   0                    0             0       0   
3                   0                    0             0       0   
4                   0                    0             0       0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0                 0                       0            0           0   
1                 0                       0            0           0   
2                 0                       0            0           0   
3                 0                       0            0           0   
4                 0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  Astrologer  \
0                    0                     0                 0           0   
1                    0                     0                 0           0   
2                    0                     0                 0           0   
3                    0                     0                 0           0   
4                    0                     0                 0           0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                   0           0                      0                    0   
1                   0           0                      0                    0   
2                   0           0                      0                    0   
3                   0           0                      0                    0   
4                   0           0                      0                    0   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  Bakery  \
0              0                0          0           0           0       0   
1              0                0          0           0           0       0   
2              0                0          0           0           0       0   
3              0                0          0           0           0       0   
4              0                0          0           0           0       0   

   Bank  Bar  Baseball Field  Baseball Stadium  Basketball Court  Bath House  \
0     0    0               0                 0                 0           0   
1     0    0               0                 0                 0           0   
2     0    0               0                 0                 0           0   
3     0    0               0                 0                 0           0   
4     0    0               0                 0                 0           0   

   Beach  Beach Bar  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0      0          0                0         0            0           0   
1      0          0                0         0            0           0   
2      0          0                0         0            0           0   
3      0          0                0         0            0           0   
4      0          0                0         0            0           0   

   Big Box Store  Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  \
0              0                         0          0           0       0   
1              0                         0          0           0       0   
2              0                         0          0           0       0   
3              0                         0         

## new dataframe size.

In [26]:
newyork_onehot.shape

(10412, 431)

#### group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [27]:
newyork_grouped = newyork_onehot.groupby('Neighborhood').mean().reset_index()
newyork_grouped

Neighborhood  Yoga Studio  Accessories Store  \
0                     Allerton     0.000000           0.000000   
1                     Annadale     0.000000           0.000000   
2                Arden Heights     0.000000           0.000000   
3                    Arlington     0.000000           0.000000   
4                     Arrochar     0.000000           0.000000   
5                      Arverne     0.000000           0.000000   
6                      Astoria     0.000000           0.000000   
7              Astoria Heights     0.000000           0.000000   
8                   Auburndale     0.000000           0.000000   
9                   Bath Beach     0.000000           0.000000   
10           Battery Park City     0.000000           0.000000   
11                   Bay Ridge     0.000000           0.000000   
12                 Bay Terrace     0.000000           0.020408   
13                  Baychester     0.000000           0.000000   
14                     Bayside     0.014085           0.000000   
15                   Bayswater     0.000000           0.000000   
16                Bedford Park     0.000000           0.000000   
17          Bedford Stuyvesant     0.000000           0.000000   
18                  Beechhurst     0.000000           0.000000   
19                    Bellaire     0.000000           0.000000   
20                Belle Harbor     0.000000           0.000000   
21                   Bellerose     0.000000           0.000000   
22                     Belmont     0.000000           0.000000   
23                 Bensonhurst     0.000000           0.000000   
24                Bergen Beach     0.000000           0.000000   
25                  Blissville     0.000000           0.000000   
26                  Bloomfield     0.000000           0.000000   
27                 Boerum Hill     0.022727           0.000000   
28                Borough Park     0.000000           0.000000   
29                Breezy Point     0.000000           0.000000   
30                   Briarwood     0.000000           0.000000   
31              Brighton Beach     0.000000           0.000000   
32               Broad Channel     0.000000           0.000000   
33           Broadway Junction     0.000000           0.000000   
34                   Bronxdale     0.000000           0.000000   
35            Brooklyn Heights     0.050000           0.000000   
36                  Brookville     0.000000           0.000000   
37                 Brownsville     0.000000           0.000000   
38                  Bulls Head     0.000000           0.000000   
39                    Bushwick     0.000000           0.000000   
40                Butler Manor     0.000000           0.000000   
41             Cambria Heights     0.000000           0.000000   
42                    Canarsie     0.000000           0.000000   
43               Carnegie Hill     0.030000           0.000000   
44             Carroll Gardens     0.000000           0.000000   
45                 Castle Hill     0.000000           0.000000   
46           Castleton Corners     0.000000           0.000000   
47              Central Harlem     0.000000           0.000000   
48                  Charleston     0.000000           0.000000   
49                     Chelsea     0.000000           0.000000   
50                   Chinatown     0.000000           0.000000   
51                 City Island     0.000000           0.000000   
52                   City Line     0.000000           0.000000   
53                Civic Center     0.030000           0.000000   
54           Claremont Village     0.000000           0.000000   
55                Clason Point     0.000000           0.000000   
56                     Clifton     0.000000           0.000000   
57                     Clinton     0.000000           0.000000   
58                Clinton Hill     0.030612           0.000000   
59                  Co-op City     0.000000           0.06

## confirm the new size

In [28]:
newyork_grouped.shape

(300, 431)

## neighborhood along with the top 10 most common venues

In [30]:
num_top_venues = 10

for hood in newyork_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = newyork_grouped[newyork_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Allerton----
                        venue  freq
0                 Pizza Place  0.11
1                 Supermarket  0.07
2               Deli / Bodega  0.07
3                         Spa  0.07
4          Chinese Restaurant  0.07
5                Dessert Shop  0.04
6  Construction & Landscaping  0.04
7          Spanish Restaurant  0.04
8              Breakfast Spot  0.04
9         Fried Chicken Joint  0.04


----Annadale----
                 venue  freq
0     Sushi Restaurant   0.1
1                Diner   0.1
2          Pizza Place   0.1
3        Train Station   0.1
4               Bakery   0.1
5           Sports Bar   0.1
6                 Park   0.1
7  American Restaurant   0.1
8        Deli / Bodega   0.1
9           Restaurant   0.1


----Arden Heights----
                 venue  freq
0             Pharmacy  0.25
1          Pizza Place  0.25
2          Coffee Shop  0.25
3             Bus Stop  0.25
4          Yoga Studio  0.00
5                 Park  0.00
6            Pet Store

## put into a *pandas* dataframe

sort the venues in descending order.

In [31]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [33]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = newyork_grouped['Neighborhood']

for ind in np.arange(newyork_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(newyork_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Allerton           Pizza Place    Chinese Restaurant   
1       Annadale                Bakery   American Restaurant   
2  Arden Heights              Pharmacy           Coffee Shop   
3      Arlington              Bus Stop         Deli / Bodega   
4       Arrochar              Bus Stop    Italian Restaurant   

  3rd Most Common Venue 4th Most Common Venue       5th Most Common Venue  \
0         Deli / Bodega           Supermarket                         Spa   
1         Train Station      Sushi Restaurant                       Diner   
2              Bus Stop           Pizza Place  Financial or Legal Service   
3   American Restaurant           Coffee Shop               Grocery Store   
4         Deli / Bodega    Athletics & Sports                 Supermarket   

  6th Most Common Venue  7th Most Common Venue 8th Most Common Venue  \
0          Intersection            Gas Station        Breakfast Spot   
1            Restaurant            Pizza Place         Deli / Bodega   
2           Event Space                Exhibit               Factory   
3            Playground          Women's Store     Fish & Chips Shop   
4        Sandwich Place  Outdoors & Recreation           Pizza Place   

  9th Most Common Venue 10th Most Common Venue  
0           Bus Station     Spanish Restaurant  
1                  Park             Sports Bar  
2    Falafel Restaurant                   Farm  
3               Factory     Falafel Restaurant  
4          Liquor Store             Bagel Shop

<a id='item4'></a>

## 4. Cluster Neighborhoods

Run *k*-means to cluster the neighborhood into 10 clusters.

In [38]:
# set number of clusters
kclusters = 10

newyork_grouped_clustering = manhattan_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 1, 1, 2, 1, 2, 2, 0, 1, 1], dtype=int32)

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [39]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

manhattan_merged = manhattan_data

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
manhattan_merged = manhattan_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

manhattan_merged.head() # check the last columns!

Borough        Neighborhood   Latitude  Longitude  Cluster Labels  \
0  Manhattan         Marble Hill  40.876551 -73.910660               1   
1  Manhattan           Chinatown  40.715618 -73.994279               1   
2  Manhattan  Washington Heights  40.851903 -73.936900               0   
3  Manhattan              Inwood  40.867684 -73.921210               0   
4  Manhattan    Hamilton Heights  40.823604 -73.949688               0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0        Sandwich Place           Coffee Shop        Discount Store   
1    Chinese Restaurant          Cocktail Bar   American Restaurant   
2                  Café     Mobile Phone Shop                Bakery   
3    Mexican Restaurant                  Café                Lounge   
4    Mexican Restaurant                  Café           Pizza Place   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0            Yoga Studio                 Diner            Steakhouse   
1  Vietnamese Restaurant    Salon / Barbershop       Bubble Tea Shop   
2          Grocery Store           Supermarket         Deli / Bodega   
3            Pizza Place                  Park                Bakery   
4            Coffee Shop          Liquor Store     Indian Restaurant   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0       Supplement Shop         Shopping Mall    Seafood Restaurant   
1                Bakery                   Spa        Ice Cream Shop   
2           Coffee Shop                  Park        Clothing Store   
3    Frozen Yogurt Shop         Deli / Bodega            Restaurant   
4      Sushi Restaurant                  Park         Deli / Bodega   

  10th Most Common Venue  
0         Tennis Stadium  
1    Dumpling Restaurant  
2     Chinese Restaurant  
3     Spanish Restaurant  
4         Sandwich Place

Finally, let's visualize the resulting clusters

In [40]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(manhattan_merged['Latitude'], manhattan_merged['Longitude'], manhattan_merged['Neighborhood'], manhattan_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

<a id='item5'></a>

## 5. Examine Clusters

Now, you can examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, you can then assign a name to each cluster. I will leave this exercise to you.

#### Cluster 1

In [41]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 0, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
2   Washington Heights                  Café     Mobile Phone Shop   
3               Inwood    Mexican Restaurant                  Café   
4     Hamilton Heights    Mexican Restaurant                  Café   
5       Manhattanville    Italian Restaurant         Deli / Bodega   
7          East Harlem    Mexican Restaurant                Bakery   
25    Manhattan Valley           Pizza Place     Indian Restaurant   
36          Tudor City                  Café    Mexican Restaurant   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
2                 Bakery         Grocery Store           Supermarket   
3                 Lounge           Pizza Place                  Park   
4            Pizza Place           Coffee Shop          Liquor Store   
5                   Park           Coffee Shop    Mexican Restaurant   
7          Deli / Bodega           Pizza Place       Thai Restaurant   
25           Coffee Shop           Yoga Studio                  Café   
36                  Park           Pizza Place      Greek Restaurant   

        6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
2               Deli / Bodega           Coffee Shop                  Park   
3                      Bakery    Frozen Yogurt Shop         Deli / Bodega   
4           Indian Restaurant      Sushi Restaurant                  Park   
5          Seafood Restaurant                  Café            Bike Trail   
7   Latin American Restaurant     French Restaurant            Steakhouse   
25         Mexican Restaurant       Thai Restaurant         Deli / Bodega   
36           Sushi Restaurant         Deli / Bodega    Spanish Restaurant   

   9th Most Common Venue 10th Most Common Venue  
2         Clothing Store     Chinese Restaurant  
3             Restaurant     Spanish Restaurant  
4          Deli / Bodega         Sandwich Place  
5                 Lounge       Sushi Restaurant  
7     Spanish Restaurant     Seafood Restaurant  
25            Playground                    Bar  
36            Restaurant           Burger Joint

#### Cluster 2

In [42]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 1, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0           Marble Hill        Sandwich Place           Coffee Shop   
1             Chinatown    Chinese Restaurant          Cocktail Bar   
6        Central Harlem    African Restaurant                   Bar   
9             Yorkville    Italian Restaurant                   Bar   
10           Lenox Hill           Coffee Shop    Italian Restaurant   
12      Upper West Side    Italian Restaurant                   Bar   
16          Murray Hill           Coffee Shop        Sandwich Place   
19         East Village                   Bar              Wine Bar   
20      Lower East Side           Coffee Shop           Pizza Place   
26  Morningside Heights                  Park           Coffee Shop   
27             Gramercy    Italian Restaurant                   Bar   
29   Financial District           Coffee Shop                 Hotel   
30        Carnegie Hill           Coffee Shop           Pizza Place   
33        Midtown South     Korean Restaurant                 Hotel   
34         Sutton Place  Gym / Fitness Center    Italian Restaurant   
35           Turtle Bay    Italian Restaurant           Coffee Shop   

     3rd Most Common Venue     4th Most Common Venue 5th Most Common Venue  \
0           Discount Store               Yoga Studio                 Diner   
1      American Restaurant     Vietnamese Restaurant    Salon / Barbershop   
6       Chinese Restaurant      Gym / Fitness Center    Seafood Restaurant   
9              Coffee Shop                       Gym           Pizza Place   
10        Sushi Restaurant               Pizza Place        Cosmetics Shop   
12                Wine Bar  Mediterranean Restaurant        Cosmetics Shop   
16                   Hotel       Japanese Restaurant    Italian Restaurant   
19          Ice Cream Shop               Pizza Place    Chinese Restaurant   
20                    Café            Sandwich Place           Art Gallery   
26     American Restaurant                 Bookstore            Food Truck   
27     American Restaurant               Pizza Place            Bagel Shop   
29               Wine Shop                       Gym   American Restaurant   
30          Cosmetics Shop                       Bar                  Café   
33            Dessert Shop       Japanese Restaurant             Hotel Bar   
34  Furniture / Home Store         Indian Restaurant             Juice Bar   
35              Steakhouse          Sushi Restaurant              Wine Bar   

   6th Most Common Venue          7th Most Common Venue 8th Most Common Venue  \
0             Steakhouse                Supplement Shop         Shopping Mall   
1        Bubble Tea Shop                         Bakery                   Spa   
6             Public Art                 Cosmetics Shop         Deli / Bodega   
9       Sushi Restaurant                      Wine Shop        Ice Cream Shop   
10          Burger Joint                            Gym  Gym / Fitness Center   
12           Coffee Shop  Vegetarian / Vegan Restaurant     Indian Restaurant   
16  Gym / Fitness Center                            Gym     French Restaurant   
19    Mexican Restaurant                   Cocktail Bar      Ramen Restaurant   
20                Bakery               Ramen Restaurant    Chinese Restaurant   
26          Tennis Court                 Sandwich Place          Burger Joint   
27          Cocktail Bar             Mexican Restaurant        Ice Cream Shop   
29           Pizza Place                     Steakhouse  Gym / Fitness Center   
30     French Restaurant            Japanese Restaurant         Grocery Store   
33   American Restaurant                    Coffee Shop        Cosmetics Shop   
34                   Gym                    Pizza Place          Dessert Shop   
35      Ramen Restaurant              Indian Restaurant   Japanese Restaurant   

   9th Most Common Venue 10th Most Common Venue  
0     Seafood Restaurant         Tennis Stadium 

#### Cluster 3

In [43]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 2, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
8     Upper East Side    Italian Restaurant               Exhibit   
13     Lincoln Square  Gym / Fitness Center               Theater   
14            Clinton               Theater  Gym / Fitness Center   
15            Midtown                 Hotel           Coffee Shop   
17            Chelsea           Coffee Shop    Italian Restaurant   
18  Greenwich Village    Italian Restaurant      Sushi Restaurant   
21            Tribeca    Italian Restaurant                  Park   
22       Little Italy                Bakery                  Café   
23               Soho        Clothing Store              Boutique   
24       West Village    Italian Restaurant        Cosmetics Shop   
28  Battery Park City                  Park           Coffee Shop   
31               Noho    Italian Restaurant     French Restaurant   
32       Civic Center    Italian Restaurant  Gym / Fitness Center   
38           Flatiron  Gym / Fitness Center                   Gym   
39       Hudson Yards   American Restaurant    Italian Restaurant   

      3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
8               Art Gallery                Bakery           Coffee Shop   
13                    Plaza                  Café          Concert Hall   
14       Italian Restaurant                 Hotel   American Restaurant   
15                  Theater        Clothing Store          Cocktail Bar   
17           Ice Cream Shop             Nightclub                Bakery   
18           Clothing Store    Seafood Restaurant     Indian Restaurant   
21                     Café   American Restaurant                   Spa   
22       Italian Restaurant        Sandwich Place       Bubble Tea Shop   
23            Women's Store           Art Gallery            Shoe Store   
24  New American Restaurant          Cocktail Bar   American Restaurant   
28                    Hotel         Memorial Site    Italian Restaurant   
31              Art Gallery          Cocktail Bar           Coffee Shop   
32        French Restaurant                 Hotel        Sandwich Place   
38              Yoga Studio   American Restaurant   Japanese Restaurant   
39                     Café  Gym / Fitness Center            Restaurant   

   6th Most Common Venue  7th Most Common Venue     8th Most Common Venue  \
8   Gym / Fitness Center              Juice Bar         French Restaurant   
13    Italian Restaurant  Performing Arts Venue                      Park   
14             Wine Shop            Coffee Shop                       Spa   
15   Sporting Goods Shop                 Bakery                 Bookstore   
17                 Hotel    American Restaurant        Seafood Restaurant   
18        Cosmetics Shop                   Café         French Restaurant   
21              Boutique               Wine Bar                       Gym   
22        Clothing Store     Salon / Barbershop  Mediterranean Restaurant   
23    Italian Restaurant            Men's Store  Mediterranean Restaurant   
24              Wine Bar                   Park                 Jazz Club   
28             Wine Shop                    Gym             Women's Store   
31             Rock Club            Pizza Place        Mexican Restaurant   
32   Sporting Goods Shop    American Restaurant                    Bakery   
38        Cosmetics Shop     Salon / Barbershop   New American Restaurant   
39    Spanish Restaurant                  Hotel                   Theater   

     9th Most Common Venue 10th Most Common Venue  
8                    Hotel                    Spa  
13             Opera House    Indie Movie Theater  
14          Sandwich Place             Food Court  
15                     Spa    Japanese Restaurant  
17             Art Gallery                Theater  
18      Chinese Restaurant           Cocktail Bar  
21        Greek Restaurant            Coffee Shop  
22          Ice Cream Shop          Women's Store  
23

#### Cluster 4

In [44]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 3, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
37  Stuyvesant Town                   Bar            Playground   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
37                  Park           Pet Service        Farmers Market   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
37      Basketball Court        Baseball Field           Gas Station   

   9th Most Common Venue 10th Most Common Venue  
37              Fountain        Harbor / Marina

#### Cluster 5

In [45]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 4, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
11  Roosevelt Island                  Park        Sandwich Place   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
11           Coffee Shop            Playground           Dry Cleaner   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
11                 Plaza                  Café        Farmers Market   

   9th Most Common Venue 10th Most Common Venue  
11           Supermarket          Metro Station

### Thank you for completing this lab!

This notebook was created by [Alex Aklson](https://www.linkedin.com/in/aklson/) and [Polong Lin](https://www.linkedin.com/in/polonglin/). I hope you found this lab interesting and educational. Feel free to contact us if you have any questions!

This notebook is part of a course on **Coursera** called *Applied Data Science Capstone*. If you accessed this notebook outside the course, you can take this course online by clicking [here](http://cocl.us/DP0701EN_Coursera_Week3_LAB2).

<hr>

Copyright &copy; 2018 [Cognitive Class](https://cognitiveclass.ai/?utm_source=bducopyrightlink&utm_medium=dswb&utm_campaign=bdu). This notebook and its source code are released under the terms of the [MIT License](https://bigdatauniversity.com/mit-license/).